<table style="width: 100%; border-style: none;">
<tr style="border-style: none">
<td style="border-style: none; width: 1%; text-align: left; font-size: 16px">Institut f&uuml;r Theoretische Physik<br /> Universit&auml;t zu K&ouml;ln</td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 16px">Prof. Dr. Simon Trebst<br />Christoph Berke</td>
</tr>
</table>
<hr>
<h1 style="font-weight:bold; text-align: center; margin: 0px; font-size: 30px; padding:0px;">Statistische Physik</h1>
<h1 style="font-weight:bold; text-align: center; margin: 0px; font-size: 30px; padding:0px;">Übungsblatt 2</h1>
<hr>
<h3 style="font-weight:bold; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px;">Wintersemester 2020/21</h3>
<hr>

**Website** [http://www.thp.uni-koeln.de/trebst/Lectures/2020-StatPhys.shtml](http://www.thp.uni-koeln.de/trebst/Lectures/2020-StatPhys.shtml)

**Abgabe**:  Montag,16.11.2020, bis 10:00 Uhr

**Besprechung**:  Dienstag, 17.11.2020

**Name**: <font color="red">Bitte geben Sie ihren Namen an</font>

**Matrikelnummer**: <font color="red">Bitte geben Sie ihre Matrikelnummer an</font>

# Simulation eines zweidimensionalen Gases

In der folgenden Aufgaben möchten wir Ihnen die Möglichkeit geben, selber die Simulation eines zweidimensionalen Gases durchzuführen. Sie sollen dabei für eine Menge an $N$ Teilchen die klassischen Bewegungsgleichungen integrieren und elastische Kollisionen zwischen den Teilchen nach Energie- und Impulserhaltung berücksichtigen. Dazu stellen wir Ihnen im Folgenden ein Framework zur Verfügung, in dem bereits alle wichtigen Funktionen implementiert sind. Ihre eigentliche Aufgabestellung finden Sie weiter unten in den Aufgabenteilen a) - d), diese werden dann vor Allem das Benutzen und Auswerten der Simulation beinhalten.

### Framework und Pakete

Stellen Sie zuerst sicher, dass Sie bereits alle wichtigen Julia-Pakete installiert haben und diese verwenden können. Sofern Sie die untere Box nicht mit der Ausgabe `true` ausführen können, installieren Sie fehlende Pakete und fahren Sie dann fort.

In [ ]:
using Random
using LinearAlgebra
using ProgressMeter
using PyPlot
pygui(true)

Führen Sie jetzt die nachfolgenden Zellen aus. Diese definieren Funktionen, welche später für eine Simulation verwendet werden. Machen Sie sich die Wirkung der einzelnen Funktionen klar und fügen Sie ggf. Kommentare ein, falls für Sie nötig.

In [ ]:
function initialize_particles!(
            x::Vector{<:Real},  y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real}, vy::Vector{<:Real}, # velocity arrays
            r::Vector{<:Real},                      # particle radius array
            v::Real,                                # particle velocity
            box::NTuple{4, Float64}                 # box = (x_min, x_max, y_min, y_max)
        )
    
    # extract minimal / maximal x and y
    x_min, x_max, y_min, y_max = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # random position with distance r to boundary
        x[i] = x_min+2*r[i] + rand()*(x_max - x_min - 4*r[i])
        y[i] = y_min+2*r[i] + rand()*(y_max - y_min - 4*r[i])
        
        # random velocity direction
        angle = rand()*2*pi
        vx[i] = cos(angle)*v
        vy[i] = sin(angle)*v
        
    end
    
end



function initialize_particles_without_overlap!(
            x::Vector{<:Real},  y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real}, vy::Vector{<:Real}, # velocity arrays
            r::Vector{<:Real},                      # particle radius array
            v::Real,                                # particle velocity
            box::NTuple{4, Float64}                 # box = (x_min, x_max, y_min, y_max)
        )
    
    # extract minimal / maximal x and y
    x_min, x_max, y_min, y_max = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # reset counter of maximal tries
        tries     = 0
        max_tries = 1000
        
        # random position with distance r to boundary and no overlap to other particles
        overlapping = true
        while overlapping
            x[i] = x_min+2*r[i] + rand()*(x_max - x_min - 4*r[i])
            y[i] = y_min+2*r[i] + rand()*(y_max - y_min - 4*r[i])
            overlapping = false
            for j in 1:i-1
                if (x[i]-x[j])^2 + (y[i]-y[j])^2 < 1.01*(r[i]+r[j])^2
                    overlapping = true
                end
            end
            tries += 1
            # maybe break loop because of maximum tries
            if tries > max_tries
                @error "Could not place particle! Exceeded $(max_tries) tries"
                return
            end
        end
        
        # random velocity direction
        angle = rand()*2*pi
        vx[i] = cos(angle)*v
        vy[i] = sin(angle)*v
        
    end
    
end

In [ ]:
function move_particles!(
            x::Vector{<:Real}, y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real},vy::Vector{<:Real}, # velocity arrays
            dt::Real,                              # time increment
            r::Vector{<:Real},                     # particle radius array
            box::NTuple{4, Float64}                # box = (x_min, x_max, y_min, y_max)
        )
    
    # move all particles by dt
    x .+= vx .* dt
    y .+= vy .* dt
    
    # check collision with bounding box
    for i in 1:length(x)
        # left / right
        if x[i]-r[i] < box[1]
            vx[i] *= -1
        elseif x[i]+r[i] > box[2]
            vx[i] *= -1
        end
        # up / down
        if y[i]-r[i] < box[3]
            vy[i] *= -1
        elseif y[i]+r[i] > box[4]
            vy[i] *= -1
        end
    end
end

In [ ]:
function collide_particles!(
            x::Vector{<:Real}, y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real},vy::Vector{<:Real}, # velocity arrays
            m::Vector{<:Real},                     # mass array
            r::Vector{<:Real},                     # particle radius array
        )
    
    # check all particle pairs (i,j) for collision
    for i in 1:length(x)
        for j in 1:i-1
            
            # particles i and j are too close --> collision
            if (x[i]-x[j])^2 + (y[i]-y[j])^2 < (r[i]+r[j])^2
                e_r = [x[j]-x[i], y[j]-y[i]]
                e_r = e_r ./ norm(e_r)
                v_i = e_r[1]*vx[i] + e_r[2]*vy[i]
                v_j = e_r[1]*vx[j] + e_r[2]*vy[j]
                v_i_p = 2*(m[i]*v_i + m[j]*v_j)/(m[i]+m[j])  -  v_i
                v_j_p = 2*(m[i]*v_i + m[j]*v_j)/(m[i]+m[j])  -  v_j
                vx[i] = vx[i] + (v_i_p - v_i)*e_r[1]
                vy[i] = vy[i] + (v_i_p - v_i)*e_r[2]
                vx[j] = vx[j] + (v_j_p - v_j)*e_r[1]
                vy[j] = vy[j] + (v_j_p - v_j)*e_r[2]
            end
            
        end
    end
    
end

### a) Ausführen einer erster Simulation

Nachdem Sie jetzt alle Funktionen definiert haben, kommen wir zur eigentlich Simulation. Führen Sie die nachfolgende Zelle aus und erklären Sie in einem kleinen Absatz Text, wie die verschiedenen Bausteine des Frameworks zu einer kompletten Simulation zusammengesetzt werden.

In [ ]:
###################
# PARAMETER
###################

# Number of particles
N = 100

# bounding box of simulation
box       = (0.0, 1.98, 0.0, 1.08)
box_start = box

# radius / velocity
radius = 0.01
v      = 0.4

# steps per frame of animation
steps_per_frame = 10
fps             = 30

# simulation time
t_max = 50.0
dt    = 1.0 / fps # (of one frame)
times = 0.0:dt:t_max


###################
# INITIAL CONDITIONS
###################

# create arrays
x  = zeros(N)
y  = zeros(N)
vx = zeros(N)
vy = zeros(N)
m  = zeros(N) .+ 1.0
r  = zeros(N) .+ radius

# initialize particles
initialize_particles_without_overlap!(x,y,vx,vy,r,v,box_start)

# setup animation
fig = figure(figsize=((box[2]-box[1])*10, (box[4]-box[3])*10), dpi=50, frameon=false)
particle_circles = [plt.Circle((x[i],y[i]), radius=r[i], linewidth=0) for i in 1:N]
gca().add_collection(matplotlib.collections.PatchCollection(particle_circles))
xlim(box[1], box[2])
ylim(box[3], box[4])
axis("off")
xticks([],[])
yticks([],[])
gcf().subplots_adjust(bottom=0, top=1, right=1, left=0)





###################
# ANIMATION
###################

# let animate
@showprogress "Animating ... " for (i,t) in enumerate(times)
    
    # perform steps_per_frame time steps
    for j in 1:steps_per_frame
        # let particles collide with each other
        collide_particles!(x,y,vx,vy,m,r)
        # let particles move
        move_particles!(x,y,vx,vy,dt/steps_per_frame,r,box)
    end
    
    # set the plotting data
    gca().collections[1].remove()
    particle_circles = [plt.Circle((x[i],y[i]), radius=r[i], linewidth=0) for i in 1:N]
    gca().add_collection(matplotlib.collections.PatchCollection(particle_circles))
    
    # show to user
    pause(0.01)
    
    # maybe abort the animation
    if length(get_fignums()) == 0
        println("window closed")
        break
    end    
    
end


# finished animation
println("--- ALL DONE ---")
close(fig)

### b) Verschiedene Anfangsbedingungen

Benutzen Sie die Simulation aus Aufgabenteil a) um im Folgenden drei verschiedene Szenarien zu untersuchen:
- Alle Teilchen starten auf der linken Seite der Box
- Alle Teilchen starten in einer Ecke der Box
- Die Hälfte der Teilchen startet ohne Geschwindigkeit (sie ruhen also)

Implementieren Sie jede Startbedingung und erzeugen Sie eine Simulation. Beurteilen Sie qualitativ, inwiefern Sie die Simulationen voneinander unterscheiden können, nachdem einige Zeit vergangen ist.